In [0]:
import datetime
import requests
import json # I find out that I need this to read the "return" from the weather API
from pyspark.sql.functions import (
    col,            
    lit,            
    when,           
    to_timestamp,   
    date_format,    
    hour,           
    dayofweek,      
    count,          
    sum             
)
from pyspark.sql.types import (
    StructType,
    StructField,
    StringType,
    IntegerType,
    DoubleType,
    TimestampType
)

print("Toolbox opened successfully 🧙‍♂️")

Toolbox opened successfully 🧙‍♂️


In [0]:
file_loc = "/Volumes/personal_projects/gru_airport/raw_data_vra/VRA_2025_01.csv"

schema_vra = StructType([
    StructField("Sigla ICAO Empresa Aérea", StringType(), True),
    StructField("Empresa Aérea", StringType(), True),
    StructField("Número Voo", IntegerType(), True),
    StructField("Código DI", StringType(), True),
    StructField("Código Tipo Linha", StringType(), True),
    StructField("Modelo Equipamento", StringType(), True),
    StructField("Número de Assentos", IntegerType(), True),  # Math numberr
    StructField("Sigla ICAO Aeroporto Origem", StringType(), True),
    StructField("Descrição Aeroporto Origem", StringType(), True),
    # Dates are initially read as strings (Brazilian format) and converted later to a standard format
    StructField("Partida Prevista", StringType(), True),
    StructField("Partida Real", StringType(), True),
    StructField("Sigla ICAO Aeroporto Destino", StringType(), True),
    StructField("Descrição Aeroporto Destino", StringType(), True),
    StructField("Chegada Prevista", StringType(), True),
    StructField("Chegada Real", StringType(), True),
    StructField("Situação Voo", StringType(), True),
    StructField("Justificativa", StringType(), True),
    StructField("Referência", StringType(), True),
    StructField("Situação Partida", StringType(), True),
    StructField("Situação Chegada", StringType(), True)
])

df_vra = (spark.read
          .format("csv")
          .option("header", "true")
          .option("delimiter", ";")
          .schema(schema_vra)
          .load(file_loc))

display(df_vra)

Sigla ICAO Empresa Aérea Empresa Aérea Número Voo Código DI Código Tipo Linha Modelo Equipamento Número de Assentos Sigla ICAO Aeroporto Origem Descrição Aeroporto Origem Partida Prevista Partida Real Sigla ICAO Aeroporto Destino Descrição Aeroporto Destino Chegada Prevista Chegada Real Situação Voo Justificativa Referência Situação Partida Situação Chegada AAL AMERICAN AIRLINES, INC. 904 0 I B788 295 SBGL AEROPORTO INTERNACIONAL DO RIO DE JANEIRO (GALEÃO) - ANTONIO CARLOS JOBIM - RIO DE JANEIRO - RJ - BRASIL 01/01/2025 23:55 01/01/2025 23:50 KMIA MIAMI INTERNATIONAL AIRPORT - MIAMI, FLORIDA - ESTADOS UNIDOS DA AMÉRICA 02/01/2025 07:45 02/01/2025 08:11 REALIZADO null 2025-01-01 Antecipado Pontual AAL AMERICAN AIRLINES, INC. 905 0 I B788 295 KMIA MIAMI INTERNATIONAL AIRPORT - MIAMI, FLORIDA - ESTADOS UNIDOS DA AMÉRICA 01/01/2025 01:10 01/01/2025 01:10 SBGL AEROPORTO INTERNACIONAL DO RIO DE JANEIRO (GALEÃO) - ANTONIO CARLOS JOBIM - RIO DE JANEIRO - RJ - BRASIL 01/01/2025 09:25 01/01/2025 09:24 REALIZADO null 2025-01-01 Pontual Antecipado AAL AMERICAN AIRLINES, INC. 906 0 I B77W 318 SBGR GUARULHOS - GOVERNADOR ANDRÉ FRANCO MONTORO - GUARULHOS - SP - BRASIL 01/01/2025 00:30 01/01/2025 00:20 KMIA MIAMI INTERNATIONAL AIRPORT - MIAMI, FLORIDA - ESTADOS UNIDOS DA AMÉRICA 01/01/2025 08:55 01/01/2025 08:31 REALIZADO null 2025-01-01 Antecipado Antecipado AAL AMERICAN AIRLINES, INC. 925 0 I B772 288 KMIA MIAMI INTERNATIONAL AIRPORT - MIAMI, FLORIDA - ESTADOS UNIDOS DA AMÉRICA 01/01/2025 23:50 02/01/2025 00:03 SBGR GUARULHOS - GOVERNADOR ANDRÉ FRANCO MONTORO - GUARULHOS - SP - BRASIL 02/01/2025 08:10 02/01/2025 08:37 REALIZADO null 2025-01-01 Pontual Pontual AAL AMERICAN AIRLINES, INC. 929 0 I B77W 318 KMIA MIAMI INTERNATIONAL AIRPORT - MIAMI, FLORIDA - ESTADOS UNIDOS DA AMÉRICA 01/01/2025 20:50 01/01/2025 22:01 SBGR GUARULHOS - GOVERNADOR ANDRÉ FRANCO MONTORO - GUARULHOS - SP - BRASIL 02/01/2025 06:20 02/01/2025 06:44 REALIZADO null 2025-01-01 Atraso 60-120 Pontual AAL AMERICAN AIRLINES, INC. 930 0 I B77W 318 SBGR GUARULHOS - GOVERNADOR ANDRÉ FRANCO MONTORO - GUARULHOS - SP - BRASIL 01/01/2025 22:30 01/01/2025 22:25 KMIA MIAMI INTERNATIONAL AIRPORT - MIAMI, FLORIDA - ESTADOS UNIDOS DA AMÉRICA 02/01/2025 06:00 02/01/2025 06:36 REALIZADO null 2025-01-01 Antecipado Atraso 30-60 AAL AMERICAN AIRLINES, INC. 936 0 I B788 295 SBGL AEROPORTO INTERNACIONAL DO RIO DE JANEIRO (GALEÃO) - ANTONIO CARLOS JOBIM - RIO DE JANEIRO - RJ - BRASIL 01/01/2025 23:00 01/01/2025 22:38 KDFW DALLAS-FORT WORTH INTERNATIONAL AIRPORT - DALLAS & FORT WORTH, TEXAS - ESTADOS UNIDOS DA AMÉRICA 02/01/2025 06:50 02/01/2025 09:19 REALIZADO null 2025-01-01 Antecipado Atraso 120-240 AAL AMERICAN AIRLINES, INC. 937 0 I B788 295 KDFW DALLAS-FORT WORTH INTERNATIONAL AIRPORT - DALLAS & FORT WORTH, TEXAS - ESTADOS UNIDOS DA AMÉRICA 01/01/2025 20:00 01/01/2025 22:09 SBGL AEROPORTO INTERNACIONAL DO RIO DE JANEIRO (GALEÃO) - ANTONIO CARLOS JOBIM - RIO DE JANEIRO - RJ - BRASIL 02/01/2025 08:00 02/01/2025 08:26 REALIZADO null 2025-01-01 Atraso 120-240 Pontual AAL AMERICAN AIRLINES, INC. 948 0 I B788 295 KMIA MIAMI INTERNATIONAL AIRPORT - MIAMI, FLORIDA - ESTADOS UNIDOS DA AMÉRICA 01/01/2025 22:10 null SBGL AEROPORTO INTERNACIONAL DO RIO DE JANEIRO (GALEÃO) - ANTONIO CARLOS JOBIM - RIO DE JANEIRO - RJ - BRASIL 02/01/2025 05:45 null CANCELADO null 2025-01-01 null null AAL AMERICAN AIRLINES, INC. 950 0 I B772 288 SBGR GUARULHOS - GOVERNADOR ANDRÉ FRANCO MONTORO - GUARULHOS - SP - BRASIL 01/01/2025 23:15 01/01/2025 22:57 KJFK JOHN F. KENNEDY INTERNATIONAL AIRPORT - NEW YORK, NEW YORK - ESTADOS UNIDOS DA AMÉRICA 02/01/2025 09:00 02/01/2025 08:29 REALIZADO null 2025-01-01 Antecipado Antecipado AAL AMERICAN AIRLINES, INC. 951 0 I B789 295 KJFK JOHN F. KENNEDY INTERNATIONAL AIRPORT - NEW YORK, NEW YORK - ESTADOS UNIDOS DA AMÉRICA 01/01/2025 20:00 01/01/2025 20:39 SBGR GUARULHOS - GOVERNADOR ANDRÉ FRANCO MONTORO - GUARULHOS - SP - BRASIL 02/01/2025 06:05 02/01/2025 06:15 REALIZADO null 2025-01-0

In [0]:
#while I was developing this, I faced one error in the df_vra.write because the data on the table was with ',;{}
#so bellow we clean the columns names and save the table with the correct columns names
new_columns = [
    "sigla_icao_empresa_aerea",
    "empresa_aerea",
    "numero_voo",
    "codigo_di",
    "codigo_tipo_linha",
    "modelo_equipamento",
    "numero_assentos",
    "sigla_icao_origem",
    "descricao_origem",
    "partida_prevista",
    "partida_real",
    "sigla_icao_destino",
    "descricao_destino",
    "chegada_prevista",
    "chegada_real",
    "situacao_voo",
    "justificativa",
    "referencia",
    "situacao_partida",
    "situacao_chegada"
]

df_vra_renamed = df_vra.toDF(*new_columns)

# Saving the table at the bronze layer
# Path: Catalog.Schema.nameofthetable

(df_vra_renamed.write
  .format("delta")
  .mode("overwrite")
  .saveAsTable("personal_projects.gru_airport.bronze_vra"))

print("Bronze Table saved successfully 🥉")

Bronze Table saved successfully 🥉
